<h3>Importing essential modules</h3>

In [141]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from msticpy.nbtools import nbinit
import category_encoders as ce
from sklearn.feature_extraction import FeatureHasher
import h2o
#from h2o.estimators import H2OIsolationForestEstimator
%matplotlib inline

<h3>Notebook setup</h3>

In [2]:
nbinit.init_notebook(namespace=globals());

# Load query providers (typically you'll be using just one)
qry_prov = QueryProvider("AzureSentinel")

Please wait. Loading Kqlmagic extension...


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [3]:
qry_prov.connect(WorkspaceConfig())

<IPython.core.display.Javascript object>

In [8]:
#initializing dataframe OfficeActivity
df_name = qry_prov.exec_query('OfficeActivity')

<h3>Entities</h3>

Account (Nominal)- SID, email, NTAcct <br>
Host (Nominal) - DNS <br>
IP address (Nominal) - IP address (v4, v6) <br>
URL (Nominal) - URL <br> 
Azure resource - ResourceID <br>
Registry key (Nominal) - Registry Key <br>
Domain name (DNS) (Nominal) - DNS <br>
File (Nominal) - file path <br>
File hash (Nominal) - MD5, SHA1, SHA256 <br>

In [9]:
#example dictionary data

entities = {"account":["column1","column2"], "host":"column1", "ip_address":"column1",
            "url":"column1","azure_resource":"column1","registry_key":"column1","domain":"column1",
            "domain":"column1","file":["column1","column2"], "file_hash":"column1"}

In [46]:
df_name

TenantId Application UserDomain UserAgent  \
0      8ecf8077-cf51-4820-aadd-14040956f35d                                    
1      8ecf8077-cf51-4820-aadd-14040956f35d                                    
2      8ecf8077-cf51-4820-aadd-14040956f35d                                    
3      8ecf8077-cf51-4820-aadd-14040956f35d                                    
4      8ecf8077-cf51-4820-aadd-14040956f35d                                    
...                                     ...         ...        ...       ...   
21101  8ecf8077-cf51-4820-aadd-14040956f35d                                    
21102  8ecf8077-cf51-4820-aadd-14040956f35d                                    
21103  8ecf8077-cf51-4820-aadd-14040956f35d                                    
21104  8ecf8077-cf51-4820-aadd-14040956f35d                                    
21105  8ecf8077-cf51-4820-aadd-14040956f35d                                    

          RecordType             TimeGenerated          Operation  \
0      ExchangeAdmin 2021-06-20 10:29:49+00:00           Set-User   
1      ExchangeAdmin 2021-06-20 11:00:18+00:00           Set-User   
2                 50 2021-06-20 11:48:15+00:00  MailItemsAccessed   
3                 50 2021-06-20 11:48:15+00:00  MailItemsAccessed   
4                 50 2021-06-20 11:41:40+00:00  MailItemsAccessed   
...              ...                       ...                ...   
21101             50 2021-07-21 09:45:09+00:00  MailItemsAccessed   
21102             50 2021-07-21 09:45:09+00:00  MailItemsAccessed   
21103             50 2021-07-21 09:45:09+00:00  MailItemsAccessed   
21104             50 2021-07-21 09:45:09+00:00  MailItemsAccessed   
21105  ExchangeAdmin 2021-07-21 10:51:08+00:00           Set-User   

                             OrganizationId  \
0      4b2462a4-bbee-495a-a0e1-f23ae524cc9c   
1      4b2462a4-bbee-495a-a0e1-f23ae524cc9c   
2      4b2462a4-bbee-495a-a0e1-f23ae524cc9c   
3      4b2462a4-bbee-495a-a0e1-f23ae524cc9c   
4      4b2462a4-bbee-495a-a0e1-f23ae524cc9c   
...                                     ...   
21101  4b2462a4-bbee-495a-a0e1-f23ae524cc9c   
21102  4b2462a4-bbee-495a-a0e1-f23ae524cc9c   
21103  4b2462a4-bbee-495a-a0e1-f23ae524cc9c   
21104  4b2462a4-bbee-495a-a0e1-f23ae524cc9c   
21105  4b2462a4-bbee-495a-a0e1-f23ae524cc9c   

                            OrganizationId_ UserType  \
0      4b2462a4-bbee-495a-a0e1-f23ae524cc9c  DcAdmin   
1      4b2462a4-bbee-495a-a0e1-f23ae524cc9c  DcAdmin   
2      4b2462a4-bbee-495a-a0e1-f23ae524cc9c  Regular   
3      4b2462a4-bbee-495a-a0e1-f23ae524cc9c  Regular   
4      4b2462a4-bbee-495a-a0e1-f23ae524cc9c  Regular   
...                                     ...      ...   
21101  4b2462a4-bbee-495a-a0e1-f23ae524cc9c  Regular   
21102  4b2462a4-bbee-495a-a0e1-f23ae524cc9c  Regular   
21103  4b2462a4-bbee-495a-a0e1-f23ae524cc9c  Regular   
21104  4b2462a4-bbee-495a-a0e1-f23ae524cc9c  Regular   
21105  4b2462a4-bbee-495a-a0e1-f23ae524cc9c  DcAdmin   

                                                               UserKey  \
0      NT AUTHORITY\SYSTEM (Microsoft.Exchange.Management.ForwardSync)   
1      NT AUTHORITY\SYSTEM (Microsoft.Exchange.Management.ForwardSync)   
2                                                     100320003F8A6FC7   
3                                                     100320003F8A6FC7   
4                                                     100320003F88D275   
...                                                                ...   
21101                                                 100320003F8A6FC7   
21102                                                 100320003F8A6FC7   
21103                                                 100320003F8A6FC7   
21104                                                 100320003F8A6FC7   
21105  NT AUTHORITY\SYSTEM (Microsoft.Exchange.Management.ForwardSync)   

      OfficeWorkload ResultStatus ResultReasonType  \
0           Exchange         True             True   
1         

<h3>Feature Engineering</h3>

In [98]:
df_selection = pd.DataFrame(df_name.loc[:,["Operation", "UserType", "ResultStatus"]])

In [83]:
pd.set_option('display.max_rows', None) 

In [110]:
df_training_copy = df_selection.copy()
print(column_encoder_modified(df_training_copy))

  (0, 193128)	1.0
  (0, 208163)	-1.0
  (0, 808786)	1.0
  (1, 193128)	1.0
  (1, 208163)	-1.0
  (1, 808786)	1.0
  (2, 194344)	-1.0
  (2, 600492)	1.0
  (2, 680626)	1.0
  (3, 194344)	-1.0
  (3, 600492)	1.0
  (3, 680626)	1.0
  (4, 194344)	-1.0
  (4, 600492)	1.0
  (4, 680626)	1.0
  (5, 194344)	-1.0
  (5, 600492)	1.0
  (5, 680626)	1.0
  (6, 194344)	-1.0
  (6, 600492)	1.0
  (6, 680626)	1.0
  (7, 193128)	1.0
  (7, 208163)	-1.0
  (7, 808786)	1.0
  (8, 194344)	-1.0
  :	:
  (21097, 680626)	1.0
  (21098, 194344)	-1.0
  (21098, 600492)	1.0
  (21098, 680626)	1.0
  (21099, 194344)	-1.0
  (21099, 600492)	1.0
  (21099, 680626)	1.0
  (21100, 194344)	-1.0
  (21100, 600492)	1.0
  (21100, 680626)	1.0
  (21101, 194344)	-1.0
  (21101, 600492)	1.0
  (21101, 680626)	1.0
  (21102, 194344)	-1.0
  (21102, 600492)	1.0
  (21102, 680626)	1.0
  (21103, 194344)	-1.0
  (21103, 600492)	1.0
  (21103, 680626)	1.0
  (21104, 194344)	-1.0
  (21104, 600492)	1.0
  (21104, 680626)	1.0
  (21105, 193128)	1.0
  (21105, 208163)	-1.0

In [117]:
#creating hashing encoder

def column_encoder(column,df):
    encoder = ce.HashingEncoder(cols = column, n_components = df[column].nunique())  #this is the hash encoder object
    df_final_encoding = encoder.fit_transform(df) #fitting the dataframe
    return df_final_encoding


In [119]:
column_encoder("ResultStatus",df_training_copy)

col_0  col_1  col_2                                   Operation  \
0          0      1      0                                    Set-User   
1          0      1      0                                    Set-User   
2          1      0      0                           MailItemsAccessed   
3          1      0      0                           MailItemsAccessed   
4          1      0      0                           MailItemsAccessed   
5          1      0      0                           MailItemsAccessed   
6          1      0      0                           MailItemsAccessed   
7          0      1      0                                    Set-User   
8          1      0      0                           MailItemsAccessed   
9          1      0      0                           MailItemsAccessed   
10         1      0      0                           MailItemsAccessed   
11         1      0      0                           MailItemsAccessed   
12         1      0      0                           MailItemsAccessed   
13         1      0      0                           MailItemsAccessed   
14         1      0      0                           MailItemsAccessed   
15         1      0      0                           MailItemsAccessed   
16         1      0      0                           MailItemsAccessed   
17         1      0      0                           MailItemsAccessed   
18         1      0      0                           MailItemsAccessed   
19         1      0      0                           MailItemsAccessed   
20         1      0      0                           MailItemsAccessed   
21         1      0      0                           MailItemsAccessed   
22         1      0      0                           MailItemsAccessed   
23         1      0      0                           MailItemsAccessed   
24         1      0      0                     ModifyFolderPermissions   
25         1      0      0                           MailItemsAccessed   
26         1      0      0                           MailItemsAccessed   
27         1      0      0                           MailItemsAccessed   
28         1      0      0                           MailItemsAccessed   
29         0      1      0                                    Set-User   
30         1      0      0                           MailItemsAccessed   
31         1      0      0                           MailItemsAccessed   
32         1      0      0                           MailItemsAccessed   
33         1      0      0                           MailItemsAccessed   
34         1      0      0                           MailItemsAccessed   
35         0      1      0                                    Set-User   
36         1      0      0                           MailItemsAccessed   
37         1      0      0                           MailItemsAccessed   
38         1      0      0                           MailItemsAccessed   
39         1      0      0                           MailItemsAccessed   
40         1      0      0                           MailItemsAccessed   
41         1      0      0                           MailItemsAccessed   
42         1      0      0                           MailItemsAccessed   
43         1      0      0                           MailItemsAccessed   
44         0      1      0                                    Set-User   
45         0      1      0                                    Set-User   
46         1      0      0                           MailItemsAccessed   
47         1      0      0                           MailItemsAccessed   
48         1      0      0                           MailItemsAccessed   
49         0      1      0                                    Set-User   
50         1      0      0                           MailItemsAccessed   
51         1      0      0                           MailItemsAccessed   
52         0      1      0                                    Set-User   
53         

<h3>Isolation Forest</h3>

In [144]:
cols = list(df_selection.columns)
hf_selection = h2o.H2OFrame(df_selection)

H2OConnectionError: Not connected to a cluster. Did you run `h2o.connect()`?

In [145]:
h2o.connect()

Connecting to H2O server at http://localhost:54321 ....... failed.


H2OConnectionError: Could not establish link to the H2O cloud http://localhost:54321 after 5 retries
[01:01.89] H2OConnectionError: Unexpected HTTP error: HTTPConnectionPool(host='localhost', port=54321): Max retries exceeded with url: /3/Cloud (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x0000020AAD4CB190>: Failed to establish a new connection: [WinError 10061] No connection could be made because the target machine actively refused it'))
[01:06.20] H2OConnectionError: Unexpected HTTP error: HTTPConnectionPool(host='localhost', port=54321): Max retries exceeded with url: /3/Cloud (Caused by NewConnectionError('<urllib3.connection.HTTPConnection object at 0x0000020AAD4CB9D0>: Failed to establish a new connection: [WinError 10061] No connection could be made because the target machine actively refused it'))
[01:10.52] H2OConnectionError: Unexpected HTTP error: HTTPConnectionPool(host='localhost', port=54321): Max retries exceeded with url: /3/Cloud (Caused

In [142]:
isolation_model = H2OIsolationForestEstimator(model_id = "isolation_forest.hex", seed = 1234)
isolation_model.train(training_frame = hf_selection, x = cols)

NameError: name 'hf_selection' is not defined

In [ ]:
"""
Maybe Code 

def column_encoder_modified(df):
    for i in df.columns:
        df[i] = df[i].astype(str)
    encoder = FeatureHasher(input_type="string")
    train=encoder.transform(df.values)
    return train 
    
"""